### Loading data from API

In [1]:
import http.client
import pandas as pd
import json
from pandas.io.json import json_normalize

conn = http.client.HTTPSConnection("api.sportradar.us")
#creating connections
#<http.client.HTTPSConnection object at 0x1070bc0f0>

#MAY 3 GAME
#conn.request("GET", "/mlb/trial/v6.5/en/games/65eea473-17f4-46e8-bbf4-18afc7456470/pbp.json?api_key=28ccg2yyuxrxcmmjf5yfkgk5")

#NEW TEST GAME
conn.request("GET", "/mlb/trial/v6.5/en/games/301bcca4-fa6e-4722-8494-78a23ec2e678/pbp.json?api_key=28ccg2yyuxrxcmmjf5yfkgk5")
#Sending the request to the server to pull the listed game, in english from v6.5.

res = conn.getresponse()
#Getting the response. 

data = res.read()

In [2]:
print(data)

b'{"game":{"id":"301bcca4-fa6e-4722-8494-78a23ec2e678","status":"closed","coverage":"full","game_number":1,"day_night":"N","scheduled":"2018-05-04T23:10:00+00:00","home_team":"f246a5e5-afdb-479c-9aaa-c68beeda7af6","away_team":"29dd9a87-5bcc-4774-80c3-7f50d985068b","attendance":34030,"duration":"3:14","double_header":false,"venue":{"name":"Citi Field","market":"New York","capacity":41922,"surface":"grass","address":"123-01 Roosevelt Avenue","city":"Flushing, Queens","state":"NY","zip":"11368","country":"USA","id":"265c7d6c-427a-4b8a-8def-392c41954bec","field_orientation":"NE","stadium_type":"outdoor","location":{"lat":"40.7564124","lng":"-73.84589369999999"}},"broadcast":{"network":"SNY"},"scoring":{"home":{"name":"Mets","market":"New York","abbr":"NYM","id":"f246a5e5-afdb-479c-9aaa-c68beeda7af6","runs":7,"hits":12,"errors":0},"away":{"name":"Rockies","market":"Colorado","abbr":"COL","id":"29dd9a87-5bcc-4774-80c3-7f50d985068b","runs":8,"hits":11,"errors":1}},"innings":[{"number":0,"sequ

### Trying jq

In [ ]:
! data | jq '.'

In [ ]:
! curl -X GET "https://api.sportradar.us/mlb/trial/v6.5/en/games/d4f1ecee-8318-42e7-8ce9-90411d089dfa/pbp.json?api_key=28ccg2yyuxrxcmmjf5yfkgk5" | jq '.'

### Trying for-loop for at_bat information

In [3]:
jason_parsed = json.loads(data)

**NOTES**
- We have successfully added all of the innings to our list!
- Each inning has a half, and we need to get to the key 'event' for each half. 
##NOTE! WHEN DOING FINAL, ONLY CHOOSE CARD'S INDEX. 
- Each 'event' has a certain number of "at_bats"... i.e. # of players who step up to the plate!
- Each player who steps up to the plate has a certain number of "events" which is pitches during their "at bat".
- Inning and score information not included at the portion pulled... added to data frame. 

**Here is the master count**
- 9 innings
- 2 events per inning
- Variable total at bats
- Variable individual pitches (not sure why my table is showing 263...)

In [300]:

#innings=[]
#halfings =[]

pitches =[]

def getcode(parsed):
    cardcounter = 0
    cubcounter = 0
    
    for inning in range(1,10):
        if 'game' in parsed.keys():
            level1 = parsed['game']['innings'][inning]
            
            for halfs in range(0,2):
                level2 = level1['halfs'][halfs]['events']
            
            #for halfs in range(1,2):
               # for c in level1['halfs'][halfs]['events']:
                 #   for cb in range(0,len(c)):
                  #      cub = c[cb]
                   #     if 'runners' in cub.keys():
                      #      if r['ending_base'] == 4:
                      #              cubcounter +=1
                  
                for i in range(0,len(level2)):
                    level3= level2[i]
                    if 'at_bat' in level3.keys():
                        
                        for x in level3['at_bat']['events']:
                            x['innings'] = inning
                            
                            #if inning > 1:
                             #   x['PointDiff'] = ((jason_parsed['game']['innings'][inning-1]['scoring']['home']['runs']) - (jason_parsed['game']['innings'][inning-1]['scoring']['away']['runs']))
                            #else: x['PointDiff'] = 0
                                
                            if 'runners' in x.keys():
                                for r in x['runners']:
#                                      print(r)
                                    if r['starting_base'] == 1:
                                        x['OnFirst'] = 1
                                    if r['starting_base'] == 2:
                                        x['OnSecond'] = 1
                                    if r['starting_base'] == 3:
                                        x['OnThird'] = 1 
                                    
                                    if r['ending_base'] == 4:
                                        if halfs == 0:
                                            cubcounter += 1
                                        if halfs == 1:
                                            cardcounter += 1
                            
                            if halfs == 0:
                                x['Team'] = 'Cubs'
                                x['Points'] = cubcounter
                            else:
                                x['Team'] = 'Cardinals'
                                x['Points'] = cardcounter
                                
                            x['PointDiff'] = cardcounter - cubcounter  
                            
                            pitches.append(x)
                            
                            
                            #level4 = level3['at_bat']['events']
                            #print(level4)
                            
                            #level4['inning'] = inning
                            #pitches.append(level4)
                            #pitches.update(level4)
                    

getcode(jason_parsed)

##NECESSARY WHEN WE DIDN'T INCLUDE IN ORIGINAL FOR LOOP
#maybe = []

#for i in pitches:
 #   for p in i:
  #      maybe.append(p)
        
    
    
#maybe
    
#pitches2 = pitches[0:]
#pitches2

hm2 = json_normalize(pitches)

#hm2['hitter.first_name']
# hm2.columns
#hm2['inning', 'pitcher.pitch_count','pitcher.pitch_type']]

# hm2["outcome_id"].unique()
# hm2['runners']

# hm2[['hit_type','hit_location']]
 
# hm2[['innings','PointDiff']]

#df = json_normalize(d, ['applications', ['answers']])

# hm2['OnFirst']

hm2

OnFirst  OnSecond  OnThird  PointDiff  Points       Team  count.balls  \
0        NaN       NaN      NaN          0       0       Cubs          1.0   
1        NaN       NaN      NaN          0       0       Cubs          1.0   
2        NaN       NaN      NaN          0       0       Cubs          1.0   
3        NaN       NaN      NaN          0       0       Cubs          1.0   
4        NaN       NaN      NaN          0       0       Cubs          2.0   
5        NaN       NaN      NaN          0       0       Cubs          2.0   
6        1.0       NaN      NaN          0       0       Cubs          0.0   
7        1.0       NaN      NaN          0       0       Cubs          1.0   
8        1.0       NaN      NaN          0       0       Cubs          1.0   
9        1.0       NaN      NaN          0       0       Cubs          1.0   
10       1.0       1.0      NaN          0       0       Cubs          0.0   
11       1.0       1.0      NaN          0       0       Cubs          0.0   
12       1.0       1.0      NaN         -1       1       Cubs          0.0   
13       1.0       NaN      1.0         -2       2       Cubs          0.0   
14       NaN       1.0      NaN         -2       2       Cubs          0.0   
15       NaN       1.0      NaN         -2       2       Cubs          1.0   
16       NaN       1.0      NaN         -3       3       Cubs          1.0   
17       NaN       1.0      NaN         -3       3       Cubs          0.0   
18       NaN       1.0      NaN         -3       3       Cubs          0.0   
19       NaN       1.0      1.0         -3       3       Cubs          0.0   
20       NaN       1.0      1.0         -3       3       Cubs          0.0   
21       NaN       1.0      1.0         -3       3       Cubs          1.0   
22       NaN       1.0      1.0         -5       5       Cubs          1.0   
23       1.0       NaN      NaN         -5       5       Cubs          0.0   
24       1.0       NaN      NaN         -5       5       Cubs          0.0   
25       1.0       NaN      NaN         -5       5       Cubs          1.0   
26       1.0       NaN      NaN         -5       5       Cubs          2.0   
27       1.0       NaN      NaN         -5       5       Cubs          2.0   
28       1.0       NaN      NaN         -5       5       Cubs          2.0   
29       1.0       NaN      NaN         -5       5       Cubs          0.0   
..       ...       ...      ...        ...     ...        ...          ...   
300      1.0       NaN      NaN         -3       5  Cardinals          1.0   
301      1.0       NaN      NaN         -3       5  Cardinals          1.0   
302      1.0       NaN      NaN         -3       5  Cardinals          0.0   
303      1.0       NaN      NaN         -3       5  Cardinals          1.0   
304      1.0       NaN      NaN         -3       5  Cardinals          1.0   
305      1.0       NaN      NaN         -3       5  Cardinals          2.0   
306      1.0       NaN      NaN         -2       6  Cardinals          2.0   
307      NaN       NaN      1.0         -2       6  Cardinals          1.0   
308      NaN       NaN      1.0         -2       6  Cardinals          1.0   
309      NaN       NaN      1.0         -2       6  Cardinals          1.0   
310      NaN       NaN      1.0         -2       6  Cardinals          1.0   
311      NaN       NaN      1.0         -2       6  Cardinals          2.0   
312      NaN       NaN      NaN         -2       6  Cardinals          NaN   
313      NaN       NaN      1.0         -2       6  Cardinals          3.0   
314      NaN       NaN      1.0         -2       6  Cardinals          3.0   
315      NaN       NaN      1.0         -2       6  Cardinals          1.0   
316      NaN       NaN      1.0         -2       6  Cardinals          2.0   
317      NaN       NaN      1.0         -2       6  Cardinals          2.0   
318      NaN       NaN      1.0         -2       6  Cardinals          3.0   
319      NaN       NaN     

**Keeping track of depth using index/key combination**

In [258]:
jp = jason_parsed['game']['innings'][9]['halfs'][1]['events'][-1]['at_bat']['events']
jp

[{'OnFirst': 1,
  'OnThird': 1,
  'PointDiff': 3,
  'count': {'balls': 0, 'outs': 2, 'pitch_count': 1, 'strikes': 1},
  'created_at': '2018-05-05T02:22:57+00:00',
  'flags': {'is_ab_over': False,
   'is_bunt': False,
   'is_bunt_shown': False,
   'is_double_play': False,
   'is_hit': False,
   'is_passed_ball': False,
   'is_triple_play': False,
   'is_wild_pitch': False},
  'hitter': {'first_name': 'Michael',
   'id': 'e5bdeb0e-38fc-4d30-8127-43d0d5b2864d',
   'jersey_number': '30',
   'last_name': 'Conforto',
   'preferred_name': 'Michael'},
  'id': '489cca33-0555-4445-b445-48e00f953c17',
  'innings': 9,
  'outcome_id': 'kKS',
  'pitcher': {'first_name': 'Wade',
   'hitter_hand': 'L',
   'id': 'ae9e0be2-30f9-4dab-ac78-f592f5a50f31',
   'jersey_number': '71',
   'last_name': 'Davis',
   'pitch_count': 25,
   'pitch_speed': 94.0,
   'pitch_type': 'FA',
   'pitch_x': 11,
   'pitch_y': 56,
   'pitch_zone': 2,
   'pitcher_hand': 'R',
   'preferred_name': 'Wade'},
  'runners': [{'ending_ba

In [200]:
df = json_normalize(jp)
df.columns

Index(['PointDiff', 'count.balls', 'count.outs', 'count.pitch_count',
       'count.strikes', 'created_at', 'flags.is_ab_over', 'flags.is_bunt',
       'flags.is_bunt_shown', 'flags.is_double_play', 'flags.is_hit',
       'flags.is_passed_ball', 'flags.is_triple_play', 'flags.is_wild_pitch',
       'hit_location', 'hit_type', 'hitter.first_name', 'hitter.id',
       'hitter.jersey_number', 'hitter.last_name', 'hitter.preferred_name',
       'id', 'innings', 'outcome_id', 'pitcher.first_name',
       'pitcher.hitter_hand', 'pitcher.id', 'pitcher.jersey_number',
       'pitcher.last_name', 'pitcher.pitch_count', 'pitcher.pitch_speed',
       'pitcher.pitch_type', 'pitcher.pitch_x', 'pitcher.pitch_y',
       'pitcher.pitch_zone', 'pitcher.pitcher_hand', 'pitcher.preferred_name',
       'runners', 'status', 'type', 'updated_at'],
      dtype='object')

**Practice calculating score difference at top of each inning**

In [216]:
jp2 = jason_parsed['game']['innings'][2]['scoring']['away']['runs']
jp2

1

**Practice counting the players on each base at each time**

In [251]:
jp3 = jason_parsed['game']['innings'][1]['halfs'][0]['events'][0]['at_bat']['events'][-1]['runners'][0]['starting_base']
jp3

0

### Weather information //  time information

In [305]:
weather = jason_parsed['game']['innings'][9]['halfs'][1]['weather']['current_conditions']
weather

{'cloud_cover': 75,
 'condition': 'Partly cloudy',
 'dew_point_f': 56,
 'humidity': 52,
 'obs_time': '2018-05-05T01:58:26.000Z',
 'temp_f': 76,
 'wind': {'direction': 'S', 'speed_mph': 12}}

In [122]:
weather_df = json_normalize(weather)
weather_df

current_conditions.cloud_cover current_conditions.condition  \
0                              75                Partly cloudy   

   current_conditions.dew_point_f  current_conditions.humidity  \
0                              56                           52   

  current_conditions.obs_time  current_conditions.temp_f  \
0    2018-05-05T01:58:26.000Z                         76   

  current_conditions.wind.direction  current_conditions.wind.speed_mph  
0                                 S                                 12

In [306]:
hm3 = hm2.assign(**{'cloud_cover': 75,
  'condition': 'Partly cloudy',
  'dew_point_f': 56,
  'humidity': 52,
  'obs_time': '2018-05-05T01:58:26.000Z',
  'temp_f': 76, 'wind_direction':'S','wind_speed':12, 'Homegame?': 1, "Nightgame?":1}
                   )

In [313]:
hm3.columns

Index(['OnFirst', 'OnSecond', 'OnThird', 'PointDiff', 'Points', 'Team',
       'count.balls', 'count.outs', 'count.pitch_count', 'count.strikes',
       'created_at', 'errors', 'fielders', 'flags.is_ab_over', 'flags.is_bunt',
       'flags.is_bunt_shown', 'flags.is_double_play', 'flags.is_hit',
       'flags.is_passed_ball', 'flags.is_triple_play', 'flags.is_wild_pitch',
       'hit_location', 'hit_type', 'hitter.first_name', 'hitter.id',
       'hitter.jersey_number', 'hitter.last_name', 'hitter.preferred_name',
       'id', 'innings', 'lineup.description', 'lineup.first_name', 'lineup.id',
       'lineup.jersey_number', 'lineup.last_name', 'lineup.order',
       'lineup.player_id', 'lineup.position', 'lineup.preferred_name',
       'lineup.team_id', 'outcome_id', 'pitcher.first_name',
       'pitcher.hitter_hand', 'pitcher.id', 'pitcher.jersey_number',
       'pitcher.last_name', 'pitcher.pitch_count', 'pitcher.pitch_speed',
       'pitcher.pitch_type', 'pitcher.pitch_x', 'pitcher.pi

In [355]:
hm3.loc[hm3['flags.is_bunt'] == 'NaN']

# hm3['OnFirst'].unique

#when is hitter id nan??
#when is pitcher id nan??
##Look for other weird NaNs and take em out! :)

Empty DataFrame
Columns: [OnFirst, OnSecond, OnThird, PointDiff, Points, Team, count.balls, count.outs, count.pitch_count, count.strikes, created_at, errors, fielders, flags.is_ab_over, flags.is_bunt, flags.is_bunt_shown, flags.is_double_play, flags.is_hit, flags.is_passed_ball, flags.is_triple_play, flags.is_wild_pitch, hit_location, hit_type, hitter.first_name, hitter.id, hitter.jersey_number, hitter.last_name, hitter.preferred_name, id, innings, lineup.description, lineup.first_name, lineup.id, lineup.jersey_number, lineup.last_name, lineup.order, lineup.player_id, lineup.position, lineup.preferred_name, lineup.team_id, outcome_id, pitcher.first_name, pitcher.hitter_hand, pitcher.id, pitcher.jersey_number, pitcher.last_name, pitcher.pitch_count, pitcher.pitch_speed, pitcher.pitch_type, pitcher.pitch_x, pitcher.pitch_y, pitcher.pitch_zone, pitcher.pitcher_hand, pitcher.preferred_name, runners, status, type, updated_at, warming_up.first_name, warming_up.id, warming_up.jersey_number, warming_up.last_name, warming_up.player_id, warming_up.preferred_name, warming_up.team_id, cloud_cover, condition, dew_point_f, humidity, obs_time, temp_f, wind_direction, wind_speed, Homegame?, Nightgame?]
Index: []

[0 rows x 75 columns]

**Replacing NaNs**

In [339]:
hm4 = hm3.fillna(value = 0, inplace=True)

In [366]:
hm3.loc[hm3['pitcher.id'] == 0]['hitter.id']

295    0
299    0
312    0
Name: hitter.id, dtype: object

**Removing NaNs**<br> (When the pitcher, or player id = 0). It seems like there are 3 junk columns. 

In [420]:
hm4 = hm3.drop(hm3.index[[295,299,312]])

**Removing Cubs hits**

In [434]:
hm4 = hm3.set_index('Team')
hm5 = hm4.drop(labels = 'Cubs')
hm5 = hm5.reset_index()

**DO SOME EDA ON THIS! IT'S INTERESTING**

In [409]:
hm4.loc[hm4['hit_type'] == 'FB']['flags.is_hit']#['hit_location']
# hm4.iloc[13]
#We did it!

13     False
18      True
36      True
57      True
132    False
134    False
163    False
176    False
181    False
183     True
192    False
224    False
274    False
275     True
284    False
286    False
293     True
306     True
Name: flags.is_hit, dtype: object

In [372]:
hm4.columns

Index(['OnFirst', 'OnSecond', 'OnThird', 'PointDiff', 'Points', 'Team',
       'count.balls', 'count.outs', 'count.pitch_count', 'count.strikes',
       'created_at', 'errors', 'fielders', 'flags.is_ab_over', 'flags.is_bunt',
       'flags.is_bunt_shown', 'flags.is_double_play', 'flags.is_hit',
       'flags.is_passed_ball', 'flags.is_triple_play', 'flags.is_wild_pitch',
       'hit_location', 'hit_type', 'hitter.first_name', 'hitter.id',
       'hitter.jersey_number', 'hitter.last_name', 'hitter.preferred_name',
       'id', 'innings', 'lineup.description', 'lineup.first_name', 'lineup.id',
       'lineup.jersey_number', 'lineup.last_name', 'lineup.order',
       'lineup.player_id', 'lineup.position', 'lineup.preferred_name',
       'lineup.team_id', 'outcome_id', 'pitcher.first_name',
       'pitcher.hitter_hand', 'pitcher.id', 'pitcher.jersey_number',
       'pitcher.last_name', 'pitcher.pitch_count', 'pitcher.pitch_speed',
       'pitcher.pitch_type', 'pitcher.pitch_x', 'pitcher.pi

**Selecting out only the rows of interest**

In [435]:
hintputs = hm5.filter(items = ['OnFirst','OnSecond','OnThird','PointDiff','Team','hitter.id', 'hitter.last_name', 'innings', 
       'pitcher.hitter_hand', 'pitcher.id', 
       'pitcher.last_name', 'pitcher.pitch_count', 'pitcher.pitch_speed',
       'pitcher.pitch_type', 
       'pitcher.pitch_zone', 'pitcher.pitcher_hand', 'dew_point_f',
       'temp_f','wind_speed',
       'Homegame?', 'Nightgame?'])

In [436]:
hintputs

OnFirst  OnSecond  OnThird  PointDiff       Team  \
0        0.0       0.0      0.0         -5  Cardinals   
1        0.0       0.0      0.0         -5  Cardinals   
2        0.0       0.0      0.0         -5  Cardinals   
3        0.0       0.0      0.0         -5  Cardinals   
4        1.0       0.0      0.0         -5  Cardinals   
5        1.0       0.0      0.0         -3  Cardinals   
6        0.0       0.0      0.0         -3  Cardinals   
7        0.0       0.0      0.0         -3  Cardinals   
8        0.0       0.0      0.0         -3  Cardinals   
9        0.0       0.0      0.0         -3  Cardinals   
10       0.0       0.0      0.0         -3  Cardinals   
11       0.0       0.0      0.0         -3  Cardinals   
12       0.0       0.0      0.0         -3  Cardinals   
13       0.0       0.0      0.0         -3  Cardinals   
14       0.0       0.0      0.0         -3  Cardinals   
15       0.0       0.0      0.0         -3  Cardinals   
16       0.0       0.0      0.0         -3  Cardinals   
17       0.0       0.0      0.0         -3  Cardinals   
18       0.0       0.0      0.0         -3  Cardinals   
19       0.0       0.0      0.0         -3  Cardinals   
20       0.0       0.0      0.0         -4  Cardinals   
21       0.0       0.0      0.0         -4  Cardinals   
22       0.0       0.0      0.0         -4  Cardinals   
23       0.0       0.0      0.0         -4  Cardinals   
24       0.0       0.0      0.0         -4  Cardinals   
25       0.0       0.0      0.0         -4  Cardinals   
26       0.0       0.0      0.0         -4  Cardinals   
27       0.0       0.0      0.0         -4  Cardinals   
28       1.0       0.0      0.0         -4  Cardinals   
29       1.0       0.0      0.0         -4  Cardinals   
..       ...       ...      ...        ...        ...   
153      1.0       0.0      0.0         -3  Cardinals   
154      1.0       0.0      0.0         -3  Cardinals   
155      1.0       0.0      0.0         -3  Cardinals   
156      1.0       0.0      0.0         -3  Cardinals   
157      1.0       0.0      0.0         -3  Cardinals   
158      1.0       0.0      0.0         -3  Cardinals   
159      1.0       0.0      0.0         -2  Cardinals   
160      0.0       0.0      1.0         -2  Cardinals   
161      0.0       0.0      1.0         -2  Cardinals   
162      0.0       0.0      1.0         -2  Cardinals   
163      0.0       0.0      1.0         -2  Cardinals   
164      0.0       0.0      1.0         -2  Cardinals   
165      0.0       0.0      0.0         -2  Cardinals   
166      0.0       0.0      1.0         -2  Cardinals   
167      0.0       0.0      1.0         -2  Cardinals   
168      0.0       0.0      1.0         -2  Cardinals   
169      0.0       0.0      1.0         -2  Cardinals   
170      0.0       0.0      1.0         -2  Cardinals   
171      0.0       0.0      1.0         -2  Cardinals   
172      0.0       0.0      1.0         -2  Cardinals   
173      1.0       0.0      1.0         -2  Cardinals   
174      1.0       0.0      1.0         -2  Cardinals   
175      1.0       0.0      1.0         -2  Cardinals   
176      1.0       0.0      1.0         -2  Cardinals   
177      1.0       0.0      1.0         -1  Cardinals   
178      1.0       0.0      1.0         -1  Cardinals   
179      1.0       0.0      1.0         -1  Cardinals   
180      1.0       0.0      1.0         -1  Cardinals   
181      1.0       0.0      1.0         -1  Cardinals   
182      0.0       1.0      1.0         -1  Cardinals   

                                hitter.id hitter.last_name  innings  \
0    bba23f9e-8aac-454a-b8ca-9373b5d1e5b8            Nimmo        1   
1    bba23f9e-8aac-454a-b8ca-9373b5d1e5b8            Nimmo        1   
2    bba23f9e-8aac-454a-b8ca-9373b5d1e5b8            Nimmo        1   
3    bba23f9e-8aac-454a-b8ca-9373b5d1e5b8            Nimmo        1   
4    63909aed-f094-4154-859f-bf45d81a5ebe          Cabrera        1   
5    63909aed-f094-4154-859f-bf45d81a5ebe   

In [437]:
houtputs = hm5.filter(items = ['flags.is_hit',
       'hit_location', 'hit_type'])

In [438]:
houtputs

flags.is_hit hit_location hit_type
0          False            0        0
1          False            0        0
2          False            0        0
3           True           14       LD
4          False            0        0
5           True            5       FB
6          False            0        0
7          False            0        0
8          False            0        0
9          False            0        0
10         False            0        0
11         False           21       GB
12         False            0        0
13         False            0        0
14         False           23       GB
15         False            0        0
16         False            0        0
17         False            0        0
18         False            0        0
19         False           18       PU
20         False            0        0
21         False            0        0
22         False            0        0
23         False            0        0
24         False            0        0
25         False            0        0
26         False            0        0
27          True           13       GB
28         False            0        0
29         False            0        0
..           ...          ...      ...
153        False            0        0
154        False           25       PU
155        False            0        0
156        False            0        0
157        False            0        0
158        False            0        0
159         True           10       FB
160        False            0        0
161        False            0        0
162        False            0        0
163        False            0        0
164        False            0        0
165            0            0        0
166        False            0        0
167        False            0        0
168        False            0        0
169        False            0        0
170        False            0        0
171        False            0        0
172        False            0        0
173        False            0        0
174        False            0        0
175        False            0        0
176        False            0        0
177         True           11       LD
178        False            0        0
179        False            0        0
180        False            0        0
181        False            0        0
182        False            0        0

[183 rows x 3 columns]

### Creating the list of games to pull

In [85]:
gameslist = [
    {'Date': '2018-05-06', 'Team' : "Cubs" , "H/A" : 'Home', "Link" : "e070f19f-5787-4bc0-b4d3-8f0c7e9a4f8a" },
    {'Date': '2018-05-05', 'Team' : "Cubs" , "H/A" : 'Home', "Link" : "e94d263b-d9bf-4521-b15b-32ac3933acc8" },
    {'Date': '2018-05-04', 'Team' : "Cubs" , "H/A" : 'Home', "Link" : "cea131ab-69b5-4461-a060-c5c0f0048648"},
    
    {'Date': '2018-05-02', 'Team' : "WhiteSox" , "H/A" : 'Home', "Link" : "722c8fe9-117c-4908-bde5-8d97b37197f1" },
    {'Date': '2018-05-01', 'Team' : "WhiteSox" ,  "H/A" : "Home",  "Link" : "81b010cc-0747-4c47-b90a-3810413de3ec"},
    
    {'Date': '2018-04-29', 'Team' : "Pirates" ,  "H/A" : "Pittsburg" ,  "Link" : "f5688e9e-257b-4a26-988b-7b268920568a"},
    {'Date': '2018-04-28', 'Team' : "Pirates" , "H/A" :  "Pittsburg", "Link" : "9ca520f9-d6a6-43ac-895a-37d174fef1cb" },
    {'Date': '2018-04-27', 'Team' : "Pirates" , "H/A" : "Pittsburg", "Link" : "801e73cc-879b-4b08-ab9b-52328df476b5"},
    
    {'Date': '2018-04-26', 'Team' : "Mets" ,"H/A" : "Home",  "Link" : "456c97f7-9eee-4913-a0e6-2f3923782278"},
    {'Date': '2018-04-25', 'Team' : "Mets" ,"H/A" : "Home" ,  "Link" : "385fc8fa-32b1-4700-bc04-d52f559ba15d"},
    {'Date': '2018-04-24', 'Team' : "Mets" ,"H/A" : "Home" ,  "Link" : "42a43856-5370-4e6f-a1a2-405b4ebae1b3" },
    
    {'Date': '2018-04-22', 'Team' : "Reds" , "H/A" : "Home" , "Link" : "65584b46-6aba-4bb2-8a9e-0076146c198c" },
    {'Date': '2018-04-21', 'Team' : "Reds" ,"H/A" : "Home",  "Link" : "f6a3ddde-280d-4be9-af87-63313cce4680" },
    {'Date': '2018-04-20', 'Team' : "Reds" ,"H/A" : "Home ",  "Link" : "145ca23f-57bb-4ee9-aec0-c5178406402e"},
    
    {'Date': '2018-04-19', 'Team' : "Cubs" , "H/A" : 'Chicago', "Link" : "9f558c81-10db-4c1f-abe7-a11d74127cf2" },
    {'Date': '2018-04-17', 'Team' : "Cubs" , "H/A" : 'Chicago', "Link" : "1b425fa2-6cc0-4da5-bfd9-d4c63e97ca1c"},
    
   # {'Date': '2018-04-15', 'Team' : "Reds" , "H/A" : 'Cincinnati', "Link" : "1b425fa2-6cc0-4da5-bfd9-d4c63e97ca1c"},
   # {'Date': '2018-04-14', 'Team' : "Reds" , "H/A" : 'Cincinnati', "Link" : "1b425fa2-6cc0-4da5-bfd9-d4c63e97ca1c"},
    
   # {'Date': '2018-04-11', 'Team' : "Brewers" , "H/A" : 'Home', "Link" : "1b425fa2-6cc0-4da5-bfd9-d4c63e97ca1c"},
   # {'Date': '2018-04-10', 'Team' : "Brewers" , "H/A" : 'Home', "Link" : "1b425fa2-6cc0-4da5-bfd9-d4c63e97ca1c"},
    
   # {'Date': '2018-04-08', 'Team' : "Diamondbacks" , "H/A" : 'Home', "Link" : "1b425fa2-6cc0-4da5-bfd9-d4c63e97ca1c"},
   # {'Date': '2018-04-07', 'Team' : "Diamondbacks" , "H/A" : 'Home', "Link" : "1b425fa2-6cc0-4da5-bfd9-d4c63e97ca1c"},
    
   # {'Date': '2018-04-17', 'Team' : "Brewers" , "H/A" : 'Milwaukee', "Link" : "1b425fa2-6cc0-4da5-bfd9-d4c63e97ca1c"},
   # {'Date': '2018-04-17', 'Team' : "Brewers" , "H/A" : 'Milwaukee', "Link" : "1b425fa2-6cc0-4da5-bfd9-d4c63e97ca1c"},
    
   # {'Date': '2018-04-1', 'Team' : "Mets" , "H/A" : 'NewYork', "Link" : "1b425fa2-6cc0-4da5-bfd9-d4c63e97ca1c"},
   # {'Date': '2018-03-31', 'Team' : "Mets" , "H/A" : 'NewYork', "Link" : "1b425fa2-6cc0-4da5-bfd9-d4c63e97ca1c"},
    
   # {'Date': '2018-03-27', 'Team' : "BlueJays" , "H/A" : 'Montreal', "Link" : "1b425fa2-6cc0-4da5-bfd9-d4c63e97ca1c"},
   # {'Date': '2018-03-26', 'Team' : "BlueJays" , "H/A" : 'Montreal', "Link" : "1b425fa2-6cc0-4da5-bfd9-d4c63e97ca1c"},
    
   # {'Date': '2018-03-25', 'Team' : "Nationals" , "H/A" : 'DC', "Link" : "1b425fa2-6cc0-4da5-bfd9-d4c63e97ca1c"},
    
   # {'Date': '2018-03-21', 'Team' : "Miami" , "H/A" : 'Montreal', "Link" : "1b425fa2-6cc0-4da5-bfd9-d4c63e97ca1c"},
    
]

In [86]:
pd.DataFrame(gameslist)

Date        H/A                                  Link      Team
0   2018-05-06       Home  e070f19f-5787-4bc0-b4d3-8f0c7e9a4f8a      Cubs
1   2018-05-05       Home  e94d263b-d9bf-4521-b15b-32ac3933acc8      Cubs
2   2018-05-04       Home  cea131ab-69b5-4461-a060-c5c0f0048648      Cubs
3   2018-05-02       Home  722c8fe9-117c-4908-bde5-8d97b37197f1  WhiteSox
4   2018-05-01       Home  81b010cc-0747-4c47-b90a-3810413de3ec  WhiteSox
5   2018-04-29  Pittsburg  f5688e9e-257b-4a26-988b-7b268920568a   Pirates
6   2018-04-28  Pittsburg  9ca520f9-d6a6-43ac-895a-37d174fef1cb   Pirates
7   2018-04-27  Pittsburg  801e73cc-879b-4b08-ab9b-52328df476b5   Pirates
8   2018-04-26       Home  456c97f7-9eee-4913-a0e6-2f3923782278      Mets
9   2018-04-25       Home  385fc8fa-32b1-4700-bc04-d52f559ba15d      Mets
10  2018-04-24       Home  42a43856-5370-4e6f-a1a2-405b4ebae1b3      Mets
11  2018-04-22       Home  65584b46-6aba-4bb2-8a9e-0076146c198c      Reds
12  2018-04-21       Home  f6a3ddde-280d-4be9-af87-63313cce4680      Reds
13  2018-04-20      Home   145ca23f-57bb-4ee9-aec0-c5178406402e      Reds
14  2018-04-19    Chicago  9f558c81-10db-4c1f-abe7-a11d74127cf2      Cubs
15  2018-04-17    Chicago  1b425fa2-6cc0-4da5-bfd9-d4c63e97ca1c      Cubs

### AWAY: 4/17/2018

#### Pulling from API

In [440]:
conn = http.client.HTTPSConnection("api.sportradar.us")
conn.request("GET", "/mlb/trial/v6.5/en/games/1b425fa2-6cc0-4da5-bfd9-d4c63e97ca1c/pbp.json?api_key=28ccg2yyuxrxcmmjf5yfkgk5")
res = conn.getresponse()
dataApr17 = res.read()


In [441]:
jason_parsed_17th = json.loads(dataApr17)

jason_parsed_17th

{'_comment': 'Generation started @ 2018-05-09 03:54:35 UTC ended @ 2018-05-09 03:54:36 UTC',
 'game': {'attendance': 35103,
  'away_team': '44671792-dc02-4fdd-a5ad-f5f17edaa9d7',
  'broadcast': {'network': 'NBC Sports Chicago'},
  'coverage': 'full',
  'day_night': 'N',
  'double_header': False,
  'duration': '3:33',
  'game_number': 1,
  'home_team': '55714da8-fcaf-4574-8443-59bfb511a524',
  'id': '1b425fa2-6cc0-4da5-bfd9-d4c63e97ca1c',
  'innings': [{'halfs': [{'events': [{'lineup': {'first_name': 'Adam',
         'id': '01719643-d44e-4d2f-aede-6fa61eb3dd50',
         'jersey_number': '50',
         'last_name': 'Wainwright',
         'order': 9,
         'player_id': 'c399c961-1b45-430c-858e-f0a33ae0af85',
         'position': 1,
         'preferred_name': 'Adam',
         'team_id': '44671792-dc02-4fdd-a5ad-f5f17edaa9d7'}},
       {'lineup': {'first_name': 'Matthew',
         'id': '0d608d20-568c-42b8-bc5e-323d88822577',
         'jersey_number': '13',
         'last_name': 'Carpen

#### Processing main DF from API

In [450]:
## AWAY GAME! CARDINALS HIT FIRST. 

pitches =[]

def getcode(parsed):
    cardcounter = 0
    cubcounter = 0
    
    for inning in range(1,10):
        if 'game' in parsed.keys():
            level1 = parsed['game']['innings'][inning]
            
            for halfs in range(0,2):
                level2 = level1['halfs'][halfs]['events']
                  
                for i in range(0,len(level2)):
                    level3= level2[i]
                    if 'at_bat' in level3.keys():
                        
                        for x in level3['at_bat']['events']:
                            x['innings'] = inning
                                
                            if 'runners' in x.keys():
                                for r in x['runners']:

                                    if r['starting_base'] == 1:
                                        x['OnFirst'] = 1
                                    if r['starting_base'] == 2:
                                        x['OnSecond'] = 1
                                    if r['starting_base'] == 3:
                                        x['OnThird'] = 1 
                                    
                                    if r['ending_base'] == 4:
                                        if halfs == 0:
                                            cardcounter += 1
                                        if halfs == 1:
                                            cubcounter += 1
                            
                            if halfs == 0:
                                x['Team'] = 'Cardinals'
                                x['Points'] = cardcounter
                            else:
                                x['Team'] = 'Cubs'
                                x['Points'] = cubcounter
                                
                            x['PointDiff'] = cardcounter - cubcounter  
                            x['GamevsCubs'] = 1
                            
                            pitches.append(x)
   # print(cardcounter)                    

getcode(jason_parsed_17th)

apr17 = json_normalize(pitches)

apr17

5


GamevsCubs  OnFirst  OnSecond  OnThird  PointDiff  Points       Team  \
0             1      NaN       NaN      NaN          0       0  Cardinals   
1             1      NaN       NaN      NaN          0       0  Cardinals   
2             1      NaN       NaN      NaN          0       0  Cardinals   
3             1      NaN       NaN      NaN          0       0  Cardinals   
4             1      NaN       NaN      NaN          0       0  Cardinals   
5             1      NaN       NaN      NaN          0       0  Cardinals   
6             1      NaN       NaN      NaN          0       0  Cardinals   
7             1      NaN       NaN      NaN          0       0  Cardinals   
8             1      NaN       NaN      NaN          0       0  Cardinals   
9             1      NaN       NaN      NaN          0       0  Cardinals   
10            1      NaN       NaN      NaN          0       0  Cardinals   
11            1      NaN       NaN      NaN          0       0  Cardinals   
12            1      NaN       NaN      NaN          0       0  Cardinals   
13            1      1.0       NaN      NaN          0       0  Cardinals   
14            1      1.0       NaN      NaN          0       0  Cardinals   
15            1      NaN       NaN      NaN          0       0       Cubs   
16            1      NaN       NaN      NaN          0       0       Cubs   
17            1      NaN       NaN      NaN          0       0       Cubs   
18            1      NaN       NaN      NaN          0       0       Cubs   
19            1      NaN       NaN      NaN          0       0       Cubs   
20            1      NaN       NaN      NaN          0       0       Cubs   
21            1      NaN       NaN      NaN          0       0       Cubs   
22            1      NaN       NaN      NaN          0       0       Cubs   
23            1      NaN       NaN      NaN          0       0       Cubs   
24            1      NaN       NaN      NaN          0       0       Cubs   
25            1      1.0       NaN      NaN          0       0       Cubs   
26            1      1.0       NaN      NaN          0       0       Cubs   
27            1      1.0       NaN      NaN          0       0       Cubs   
28            1      NaN       NaN      NaN          0       0  Cardinals   
29            1      NaN       NaN      NaN          0       0  Cardinals   
..          ...      ...       ...      ...        ...     ...        ...   
333           1      NaN       NaN      NaN          2       5  Cardinals   
334           1      NaN       NaN      NaN          2       5  Cardinals   
335           1      NaN       NaN      NaN          2       5  Cardinals   
336           1      NaN       NaN      NaN          2       5  Cardinals   
337           1      NaN       NaN      NaN          2       5  Cardinals   
338           1      NaN       NaN      NaN          2       5  Cardinals   
339           1      NaN       NaN      NaN          2       5  Cardinals   
340           1      NaN       NaN      NaN          2       5  Cardinals   
341           1      NaN       NaN      NaN          2       5  Cardinals   
342           1      NaN       NaN      NaN          2       5  Cardinals   
343           1      NaN       NaN      NaN          2       5  Cardinals   
344           1      1.0       NaN      NaN          2       5  Cardinals   
345           1      1.0       NaN      NaN          2       5  Cardinals   
346           1      1.0       NaN      NaN          2       5  Cardinals   
347           1      NaN       NaN      NaN          2       3       Cubs   
348           1      NaN       NaN      NaN          2       3       Cubs   
349           1      NaN       NaN      NaN          2       3       Cubs   
350           1      NaN       NaN      NaN          2       3       Cubs   
351           1      NaN       NaN      NaN          2       3       Cubs   
352           1      NaN       NaN      NaN          2       3       Cubs   
3

#### Getting weather // Time info 

In [462]:
weather17 = jason_parsed_17th['game']['innings'][4]['halfs'][1]['weather']['current_conditions']
weather17

{'cloud_cover': 50,
 'condition': 'Partly cloudy',
 'dew_point_f': 20,
 'humidity': 46,
 'obs_time': '2018-04-18T01:24:07.000Z',
 'temp_f': 40,
 'wind': {'direction': 'E', 'speed_mph': 9}}

In [463]:
apr17 = apr17.assign(**{'cloud_cover': 50,
  'condition': 'Partly cloudy',
  'dew_point_f': 20,
  'humidity': 46,
  'obs_time': '2018-05-05T01:58:26.000Z',
  'temp_f': 40, 'wind_direction':'E','wind_speed':9, 'Homegame?': 0, "Nightgame?":1}
                   )

In [466]:
#Just in case!
apr17.to_csv('apr17th', index_label=None)

### AWAY: 4/19/2018

#### Pulling from API

In [467]:
conn = http.client.HTTPSConnection("api.sportradar.us")
conn.request("GET", "/mlb/trial/v6.5/en/games/9f558c81-10db-4c1f-abe7-a11d74127cf2/pbp.json?api_key=28ccg2yyuxrxcmmjf5yfkgk5")
res = conn.getresponse()
dataApr19 = res.read()


In [469]:
jason_parsed_19th = json.loads(dataApr19)

jason_parsed_19th

{'_comment': 'Generation started @ 2018-05-09 04:20:27 UTC ended @ 2018-05-09 04:20:28 UTC',
 'game': {'attendance': 29648,
  'away_team': '44671792-dc02-4fdd-a5ad-f5f17edaa9d7',
  'broadcast': {'network': 'ABC 7'},
  'coverage': 'full',
  'day_night': 'D',
  'double_header': False,
  'duration': '3:10',
  'game_number': 1,
  'home_team': '55714da8-fcaf-4574-8443-59bfb511a524',
  'id': '9f558c81-10db-4c1f-abe7-a11d74127cf2',
  'innings': [{'halfs': [{'events': [{'lineup': {'first_name': 'William',
         'id': '26cdeb20-14fa-48cd-a3d1-03e8de904348',
         'jersey_number': '25',
         'last_name': 'Fowler',
         'order': 1,
         'player_id': 'a91b5de2-7809-4c9c-b67a-409835c5f17e',
         'position': 9,
         'preferred_name': 'Dexter',
         'team_id': '44671792-dc02-4fdd-a5ad-f5f17edaa9d7'}},
       {'lineup': {'first_name': 'Jedd',
         'id': '3988ff50-2c09-4bb9-a4f9-4b44738c606e',
         'jersey_number': '3',
         'last_name': 'Gyorko',
         'ord

#### Processing main DF from API

In [478]:
## AWAY GAME! CARDINALS HIT FIRST. 

pitches =[]

def getcode(parsed):
    cardcounter = 0
    cubcounter = 0
    
    for inning in range(1,10):
        if 'game' in parsed.keys():
            level1 = parsed['game']['innings'][inning]
            
            for halfs in range(0,2):
                level2 = level1['halfs'][halfs]['events']
                  
                for i in range(0,len(level2)):
                    level3= level2[i]
                    if 'at_bat' in level3.keys():
                        
                        for x in level3['at_bat']['events']:
                            x['innings'] = inning
                                
                            if 'runners' in x.keys():
                                for r in x['runners']:

                                    if r['starting_base'] == 1:
                                        x['OnFirst'] = 1
                                    if r['starting_base'] == 2:
                                        x['OnSecond'] = 1
                                    if r['starting_base'] == 3:
                                        x['OnThird'] = 1 
                                    
                                    if r['ending_base'] == 4:
                                        if halfs == 0:
                                            cardcounter += 1
                                        if halfs == 1:
                                            cubcounter += 1
                            
                            if halfs == 0:
                                x['Team'] = 'Cardinals'
                                x['Points'] = cardcounter
                            else:
                                x['Team'] = 'Cubs'
                                x['Points'] = cubcounter
                                
                            x['PointDiff'] = cardcounter - cubcounter  
                            x['GamevsCubs'] = 2
                            
                            pitches.append(x)
    print(cardcounter)                    

getcode(jason_parsed_19th)

apr19 = json_normalize(pitches)

apr19

5


GamevsCubs  OnFirst  OnSecond  OnThird  PointDiff  Points       Team  \
0             2      NaN       NaN      NaN          0       0  Cardinals   
1             2      NaN       NaN      NaN          0       0  Cardinals   
2             2      NaN       NaN      NaN          0       0  Cardinals   
3             2      NaN       NaN      NaN          0       0  Cardinals   
4             2      NaN       NaN      NaN          0       0  Cardinals   
5             2      NaN       NaN      NaN          0       0  Cardinals   
6             2      1.0       NaN      NaN          0       0  Cardinals   
7             2      1.0       NaN      NaN          0       0  Cardinals   
8             2      NaN       NaN      1.0          0       0  Cardinals   
9             2      NaN       NaN      1.0          0       0  Cardinals   
10            2      NaN       NaN      1.0          0       0  Cardinals   
11            2      NaN       NaN      1.0          0       0  Cardinals   
12            2      NaN       NaN      1.0          0       0  Cardinals   
13            2      NaN       NaN      1.0          0       0  Cardinals   
14            2      NaN       NaN      1.0          1       1  Cardinals   
15            2      NaN       NaN      NaN          1       1  Cardinals   
16            2      NaN       NaN      NaN          1       1  Cardinals   
17            2      NaN       NaN      NaN          1       0       Cubs   
18            2      NaN       NaN      NaN          1       0       Cubs   
19            2      NaN       NaN      NaN          1       0       Cubs   
20            2      NaN       NaN      NaN          1       0       Cubs   
21            2      NaN       NaN      NaN          1       0       Cubs   
22            2      NaN       NaN      NaN          1       0       Cubs   
23            2      NaN       NaN      NaN          1       0       Cubs   
24            2      NaN       NaN      1.0          1       0       Cubs   
25            2      NaN       NaN      1.0          1       0       Cubs   
26            2      NaN       NaN      1.0          1       0       Cubs   
27            2      NaN       NaN      1.0          1       0       Cubs   
28            2      NaN       NaN      1.0          0       1       Cubs   
29            2      1.0       NaN      NaN          0       1       Cubs   
..          ...      ...       ...      ...        ...     ...        ...   
302           2      1.0       1.0      NaN         -3       5  Cardinals   
303           2      1.0       1.0      NaN         -3       5  Cardinals   
304           2      1.0       1.0      NaN         -3       5  Cardinals   
305           2      1.0       1.0      NaN         -3       5  Cardinals   
306           2      1.0       1.0      NaN         -3       5  Cardinals   
307           2      NaN       NaN      NaN         -3       8       Cubs   
308           2      NaN       NaN      NaN         -3       8       Cubs   
309           2      NaN       NaN      NaN         -3       8       Cubs   
310           2      NaN       NaN      NaN         -3       8       Cubs   
311           2      NaN       NaN      NaN         -3       8       Cubs   
312           2      NaN       NaN      NaN         -3       8       Cubs   
313           2      NaN       NaN      NaN         -3       8       Cubs   
314           2      1.0       NaN      NaN         -3       8       Cubs   
315           2      1.0       NaN      NaN         -3       8       Cubs   
316           2      1.0       NaN      NaN         -3       8       Cubs   
317           2      1.0       NaN      NaN         -3       8       Cubs   
318           2      1.0       NaN      NaN         -3       8       Cubs   
319           2      NaN       NaN      NaN         -3       5  Cardinals   
320           2      NaN       NaN      NaN         -3       5  Cardinals   
321           2      NaN       NaN      NaN         -3       5  Cardinals   
3

#### Getting weather // time info

In [473]:
weather19 = jason_parsed_19th['game']['innings'][4]['halfs'][1]['weather']['current_conditions']
weather19

{'cloud_cover': 25,
 'condition': 'Partly cloudy',
 'dew_point_f': 27,
 'humidity': 38,
 'obs_time': '2018-04-19T19:37:13.000Z',
 'temp_f': 52,
 'wind': {'direction': 'NNW', 'speed_mph': 11}}

In [ ]:
apr19 = apr19.assign(**{'cloud_cover': 25,
  'condition': 'Partly cloudy',
  'dew_point_f': 27,
  'humidity': 38,
  'obs_time': '2018-05-05T01:58:26.000Z',
  'temp_f': 52, 'wind_direction':'E','wind_speed':11, 'Homegame?': 0, "Nightgame?":0}
                   )

In [479]:
apr19.to_csv('apr19', index_label = None)

### HOME: 5/4/2018

#### Pulling from API

In [480]:
conn = http.client.HTTPSConnection("api.sportradar.us")
conn.request("GET", "/mlb/trial/v6.5/en/games/cea131ab-69b5-4461-a060-c5c0f0048648/pbp.json?api_key=28ccg2yyuxrxcmmjf5yfkgk5")
res = conn.getresponse()
dataMay4 = res.read()

In [481]:
jason_parsed_4th = json.loads(dataMay4)

jason_parsed_4th

{'_comment': 'Generation started @ 2018-05-09 04:35:56 UTC ended @ 2018-05-09 04:35:56 UTC',
 'game': {'attendance': 46099,
  'away_team': '55714da8-fcaf-4574-8443-59bfb511a524',
  'broadcast': {'network': 'FS-MW'},
  'coverage': 'full',
  'day_night': 'N',
  'double_header': False,
  'duration': '2:58',
  'game_number': 1,
  'home_team': '44671792-dc02-4fdd-a5ad-f5f17edaa9d7',
  'id': 'cea131ab-69b5-4461-a060-c5c0f0048648',
  'innings': [{'halfs': [{'events': [{'lineup': {'first_name': 'Kyle',
         'id': '0f59448b-7db4-4cfa-848d-19de12cc47e0',
         'jersey_number': '12',
         'last_name': 'Schwarber',
         'order': 5,
         'player_id': 'c3d9c2d5-8100-409b-a7ea-d5bf7931fc14',
         'position': 7,
         'preferred_name': 'Kyle',
         'team_id': '55714da8-fcaf-4574-8443-59bfb511a524'}},
       {'lineup': {'first_name': 'Jason',
         'id': '4833055e-658c-4f51-be71-c38134d21bc7',
         'jersey_number': '22',
         'last_name': 'Heyward',
         'or

#### Processing Main DF

In [483]:
## HOME GAME! CARDINALS HIT SECOND.

pitches =[]

def getcode(parsed):
    cardcounter = 0
    cubcounter = 0
    
    for inning in range(1,10):
        if 'game' in parsed.keys():
            level1 = parsed['game']['innings'][inning]
            
            for halfs in range(0,2):
                level2 = level1['halfs'][halfs]['events']
                  
                for i in range(0,len(level2)):
                    level3= level2[i]
                    if 'at_bat' in level3.keys():
                        
                        for x in level3['at_bat']['events']:
                            x['innings'] = inning
                                
                            if 'runners' in x.keys():
                                for r in x['runners']:

                                    if r['starting_base'] == 1:
                                        x['OnFirst'] = 1
                                    if r['starting_base'] == 2:
                                        x['OnSecond'] = 1
                                    if r['starting_base'] == 3:
                                        x['OnThird'] = 1 
                                    
                                    if r['ending_base'] == 4:
                                        if halfs == 1:
                                            cardcounter += 1
                                        if halfs == 0:
                                            cubcounter += 1
                            
                            if halfs == 1:
                                x['Team'] = 'Cardinals'
                                x['Points'] = cardcounter
                            else:
                                x['Team'] = 'Cubs'
                                x['Points'] = cubcounter
                                
                            x['PointDiff'] = cardcounter - cubcounter  
                            x['GamevsCubs'] = 3
                            
                            pitches.append(x)
   # print(cardcounter)                    

getcode(jason_parsed_4th)

May4 = json_normalize(pitches)

May4

GamevsCubs  OnFirst  OnSecond  OnThird  PointDiff  Points       Team  \
0             3      NaN       NaN      NaN          0       0       Cubs   
1             3      NaN       NaN      NaN          0       0       Cubs   
2             3      1.0       NaN      NaN          0       0       Cubs   
3             3      1.0       NaN      NaN          0       0       Cubs   
4             3      1.0       NaN      NaN          0       0       Cubs   
5             3      1.0       NaN      NaN          0       0       Cubs   
6             3      1.0       NaN      NaN          0       0       Cubs   
7             3      1.0       NaN      NaN          0       0       Cubs   
8             3      1.0       NaN      NaN          0       0       Cubs   
9             3      1.0       NaN      NaN          0       0       Cubs   
10            3      1.0       NaN      NaN          0       0       Cubs   
11            3      1.0       NaN      NaN          0       0       Cubs   
12            3      1.0       NaN      NaN          0       0       Cubs   
13            3      1.0       NaN      NaN          0       0       Cubs   
14            3      1.0       NaN      NaN          0       0       Cubs   
15            3      NaN       1.0      NaN          0       0       Cubs   
16            3      NaN       1.0      NaN          0       0       Cubs   
17            3      NaN       1.0      NaN          0       0       Cubs   
18            3      NaN       NaN      NaN          0       0  Cardinals   
19            3      NaN       NaN      NaN          0       0  Cardinals   
20            3      NaN       NaN      NaN          0       0  Cardinals   
21            3      NaN       NaN      NaN          0       0  Cardinals   
22            3      NaN       NaN      NaN          0       0  Cardinals   
23            3      NaN       NaN      NaN          0       0  Cardinals   
24            3      NaN       NaN      NaN          0       0  Cardinals   
25            3      NaN       NaN      NaN          0       0  Cardinals   
26            3      NaN       NaN      NaN          0       0  Cardinals   
27            3      NaN       NaN      NaN          0       0  Cardinals   
28            3      NaN       NaN      NaN          0       0  Cardinals   
29            3      NaN       NaN      NaN          0       0  Cardinals   
..          ...      ...       ...      ...        ...     ...        ...   
257           3      NaN       NaN      NaN          3       0       Cubs   
258           3      NaN       1.0      NaN          3       0       Cubs   
259           3      NaN       1.0      NaN          3       0       Cubs   
260           3      NaN       1.0      NaN          3       0       Cubs   
261           3      NaN       NaN      NaN          3       3  Cardinals   
262           3      NaN       NaN      NaN          3       3  Cardinals   
263           3      NaN       NaN      NaN          3       3  Cardinals   
264           3      NaN       NaN      NaN          3       3  Cardinals   
265           3      NaN       NaN      NaN          3       3  Cardinals   
266           3      1.0       NaN      NaN          3       3  Cardinals   
267           3      1.0       NaN      NaN          3       3  Cardinals   
268           3      1.0       NaN      NaN          3       3  Cardinals   
269           3      1.0       NaN      NaN          3       3  Cardinals   
270           3      NaN       NaN      NaN          3       3  Cardinals   
271           3      NaN       NaN      NaN          3       0       Cubs   
272           3      NaN       NaN      NaN          3       0       Cubs   
273           3      NaN       NaN      NaN          3       0       Cubs   
274           3      NaN       NaN      NaN          3       0       Cubs   
275           3      1.0       NaN      NaN          3       0       Cubs   
276           3      1.0       NaN      NaN          3       0       Cubs   
2

#### Getting weather // time info

In [485]:
weather4 = jason_parsed_4th['game']['innings'][4]['halfs'][1]['weather']['current_conditions']
weather4

{'cloud_cover': 0,
 'condition': 'Clear',
 'dew_point_f': 52,
 'humidity': 57,
 'obs_time': '2018-05-05T01:31:03.000Z',
 'temp_f': 68,
 'wind': {'direction': 'N', 'speed_mph': 8}}

In [486]:
May4 = May4.assign(**{'cloud_cover': 0,
  'condition': 'Clear',
  'dew_point_f': 52,
  'humidity': 57,
  'obs_time': '2018-05-05T01:31:03.000Z',
  'temp_f': 68, 'wind_direction':'N','wind_speed':8, 'Homegame?': 1, "Nightgame?":1}
                   )

In [487]:
May4.to_csv('may4', index_label = None)

### HOME: 5/5/2018

#### Pulling from API

In [488]:
conn = http.client.HTTPSConnection("api.sportradar.us")
conn.request("GET", "/mlb/trial/v6.5/en/games/e94d263b-d9bf-4521-b15b-32ac3933acc8/pbp.json?api_key=28ccg2yyuxrxcmmjf5yfkgk5")
res = conn.getresponse()
dataMay5 = res.read()

In [489]:
jason_parsed_5th = json.loads(dataMay5)

jason_parsed_5th

{'_comment': 'Generation started @ 2018-05-09 04:43:43 UTC ended @ 2018-05-09 04:43:43 UTC',
 'game': {'attendance': 47154,
  'away_team': '55714da8-fcaf-4574-8443-59bfb511a524',
  'broadcast': {'network': 'FS-MW'},
  'coverage': 'full',
  'day_night': 'D',
  'double_header': False,
  'duration': '3:42',
  'game_number': 1,
  'home_team': '44671792-dc02-4fdd-a5ad-f5f17edaa9d7',
  'id': 'e94d263b-d9bf-4521-b15b-32ac3933acc8',
  'innings': [{'halfs': [{'events': [{'lineup': {'first_name': 'Benjamin',
         'id': '07c5b7a5-5ea3-4d03-be0e-689a0c22b137',
         'jersey_number': '18',
         'last_name': 'Zobrist',
         'order': 1,
         'player_id': '13987736-aaaa-4d5b-a126-5158e2202fe2',
         'position': 9,
         'preferred_name': 'Ben',
         'team_id': '55714da8-fcaf-4574-8443-59bfb511a524'}},
       {'lineup': {'first_name': 'Addison',
         'id': '1ce0dbd2-4e5e-40cb-b156-c6e1b9c6747f',
         'jersey_number': '27',
         'last_name': 'Russell',
         

#### Processing main DF

In [518]:
## HOME GAME! CARDINALS HIT SECOND.

pitches =[]

def getcode(parsed):
    cardcounter = 0
    cubcounter = 0
    
    for inning in range(1,10):
        if 'game' in parsed.keys():
            level1 = parsed['game']['innings'][inning]
            
            for halfs in range(0,2):
                level2 = level1['halfs'][halfs]['events']
                  
                for i in range(0,len(level2)):
                    level3= level2[i]
                    if 'at_bat' in level3.keys():
                        
                        for x in level3['at_bat']['events']:
                            x['innings'] = inning
                                
                            if 'runners' in x.keys():
                                for r in x['runners']:

                                    if r['starting_base'] == 1:
                                        x['OnFirst'] = 1
                                    if r['starting_base'] == 2:
                                        x['OnSecond'] = 1
                                    if r['starting_base'] == 3:
                                        x['OnThird'] = 1 
                                    
                                    if r['ending_base'] == 4:
                                        if halfs == 1:
                                            cardcounter += 1
                                            
                                        if halfs == 0:
                                            cubcounter += 1
                                        
                            
                            if halfs == 1:
                                x['Team'] = 'Cardinals'
                                x['Points'] = cardcounter
                            else:
                                x['Team'] = 'Cubs'
                                x['Points'] = cubcounter
                                
                            x['PointDiff'] = cardcounter - cubcounter  
                            x['GamevsCubs'] = 4
                            
                            pitches.append(x)
    print(cubcounter)                    

getcode(jason_parsed_5th)

May5 = json_normalize(pitches)

May5

6


GamevsCubs  OnFirst  OnSecond  OnThird  PointDiff  Points       Team  \
0             4      NaN       NaN      NaN          0       0       Cubs   
1             4      NaN       NaN      NaN          0       0       Cubs   
2             4      NaN       NaN      NaN          0       0       Cubs   
3             4      NaN       NaN      NaN          0       0       Cubs   
4             4      1.0       NaN      NaN          0       0       Cubs   
5             4      1.0       NaN      NaN          0       0       Cubs   
6             4      1.0       NaN      NaN          0       0       Cubs   
7             4      1.0       NaN      NaN          0       0       Cubs   
8             4      1.0       NaN      NaN          0       0       Cubs   
9             4      1.0       NaN      NaN          0       0       Cubs   
10            4      1.0       NaN      NaN          0       0       Cubs   
11            4      1.0       NaN      NaN          0       0       Cubs   
12            4      1.0       NaN      NaN          0       0       Cubs   
13            4      1.0       NaN      NaN          0       0       Cubs   
14            4      NaN       1.0      NaN          0       0       Cubs   
15            4      NaN       NaN      NaN          0       0  Cardinals   
16            4      NaN       NaN      NaN          0       0  Cardinals   
17            4      NaN       NaN      NaN          0       0  Cardinals   
18            4      NaN       NaN      NaN          0       0  Cardinals   
19            4      NaN       NaN      NaN          0       0  Cardinals   
20            4      NaN       NaN      NaN          0       0  Cardinals   
21            4      1.0       NaN      NaN          0       0  Cardinals   
22            4      1.0       NaN      NaN          0       0  Cardinals   
23            4      1.0       NaN      NaN          0       0  Cardinals   
24            4      1.0       NaN      NaN          0       0  Cardinals   
25            4      1.0       NaN      NaN          0       0  Cardinals   
26            4      NaN       1.0      NaN          0       0  Cardinals   
27            4      NaN       1.0      NaN          0       0  Cardinals   
28            4      1.0       1.0      NaN          0       0  Cardinals   
29            4      1.0       1.0      NaN          0       0  Cardinals   
..          ...      ...       ...      ...        ...     ...        ...   
291           4      NaN       1.0      NaN         -1       6       Cubs   
292           4      NaN       1.0      NaN         -1       6       Cubs   
293           4      NaN       1.0      NaN         -1       6       Cubs   
294           4      NaN       1.0      NaN         -1       6       Cubs   
295           4      NaN       1.0      NaN         -1       6       Cubs   
296           4      NaN       NaN      1.0         -1       6       Cubs   
297           4      NaN       NaN      1.0         -1       6       Cubs   
298           4      NaN       NaN      NaN         -1       5  Cardinals   
299           4      NaN       NaN      NaN         -1       5  Cardinals   
300           4      NaN       NaN      NaN         -1       5  Cardinals   
301           4      NaN       NaN      NaN         -1       5  Cardinals   
302           4      NaN       NaN      NaN         -1       5  Cardinals   
303           4      NaN       NaN      NaN         -1       5  Cardinals   
304           4      1.0       NaN      NaN         -1       5  Cardinals   
305           4      1.0       NaN      NaN         -1       5  Cardinals   
306           4      1.0       NaN      NaN         -1       5  Cardinals   
307           4      1.0       NaN      NaN         -1       5  Cardinals   
308           4      1.0       NaN      NaN         -1       5  Cardinals   
309           4      1.0       NaN      NaN         -1       5  Cardinals   
310           4      1.0       NaN      NaN         -1       5  Cardinals   
3

#### Getting weather // time

In [499]:
weather5 = jason_parsed_5th['game']['innings'][4]['halfs'][1]['weather']['current_conditions']
weather5

{'cloud_cover': 50,
 'condition': 'Partly cloudy',
 'dew_point_f': 46,
 'humidity': 30,
 'obs_time': '2018-05-05T19:38:30.000Z',
 'temp_f': 80,
 'wind': {'direction': 'NW', 'speed_mph': 0}}

In [ ]:
May5 = May5.assign(**{'cloud_cover': 0,
  'condition': 'Partly cloudy',
  'dew_point_f': 46,
  'humidity': 30,
  'obs_time': '2018-05-05T19:38:30.000Z',
  'temp_f': 80, 'wind_direction':'NW','wind_speed':0, 'Homegame?': 1, "Nightgame?":0}
                   )

In [ ]:
May5.to_csv('may5', index_label = None)

### HOME: 5/6/2018

#### Pulling from API

In [502]:
conn = http.client.HTTPSConnection("api.sportradar.us")
conn.request("GET", "/mlb/trial/v6.5/en/games/e070f19f-5787-4bc0-b4d3-8f0c7e9a4f8a/pbp.json?api_key=28ccg2yyuxrxcmmjf5yfkgk5")
res = conn.getresponse()
dataMay6 = res.read()

In [503]:
jason_parsed_6th = json.loads(dataMay6)

jason_parsed_6th

{'_comment': 'Generation started @ 2018-05-09 05:02:29 UTC ended @ 2018-05-09 05:02:30 UTC',
 'game': {'attendance': 45438,
  'away_team': '55714da8-fcaf-4574-8443-59bfb511a524',
  'broadcast': {'network': 'ESPN'},
  'coverage': 'full',
  'day_night': 'N',
  'double_header': False,
  'duration': '4:46',
  'game_number': 1,
  'home_team': '44671792-dc02-4fdd-a5ad-f5f17edaa9d7',
  'id': 'e070f19f-5787-4bc0-b4d3-8f0c7e9a4f8a',
  'innings': [{'halfs': [{'events': [{'lineup': {'first_name': 'Jonathan',
         'id': '0d4e66ad-364b-4424-9ddc-60a520f3b3fa',
         'jersey_number': '34',
         'last_name': 'Lester',
         'order': 9,
         'player_id': '46734ad0-e55b-4e2f-8a0d-72387470fcdf',
         'position': 1,
         'preferred_name': 'Jon',
         'team_id': '55714da8-fcaf-4574-8443-59bfb511a524'}},
       {'lineup': {'first_name': 'Ian',
         'id': '3ecbf086-0d08-497a-83f4-860caa008874',
         'jersey_number': '8',
         'last_name': 'Happ',
         'order': 6

#### Processing main DF

In [504]:
## HOME GAME! CARDINALS HIT SECOND.

pitches =[]

def getcode(parsed):
    cardcounter = 0
    cubcounter = 0
    
    for inning in range(1,15):
        if 'game' in parsed.keys():
            level1 = parsed['game']['innings'][inning]
            
            for halfs in range(0,2):
                level2 = level1['halfs'][halfs]['events']
                  
                for i in range(0,len(level2)):
                    level3= level2[i]
                    if 'at_bat' in level3.keys():
                        
                        for x in level3['at_bat']['events']:
                            x['innings'] = inning
                                
                            if 'runners' in x.keys():
                                for r in x['runners']:

                                    if r['starting_base'] == 1:
                                        x['OnFirst'] = 1
                                    if r['starting_base'] == 2:
                                        x['OnSecond'] = 1
                                    if r['starting_base'] == 3:
                                        x['OnThird'] = 1 
                                    
                                    if r['ending_base'] == 4:
                                        if halfs == 1:
                                            cardcounter += 1
                                        if halfs == 0:
                                            cubcounter += 1
                            
                            if halfs == 1:
                                x['Team'] = 'Cardinals'
                                x['Points'] = cardcounter
                            else:
                                x['Team'] = 'Cubs'
                                x['Points'] = cubcounter
                                
                            x['PointDiff'] = cardcounter - cubcounter  
                            x['GamevsCubs'] = 5
                            
                            pitches.append(x)
   # print(cardcounter)                    

getcode(jason_parsed_6th)

May6 = json_normalize(pitches)

May6

GamevsCubs  OnFirst  OnSecond  OnThird  PointDiff  Points       Team  \
0             5      NaN       NaN      NaN          0       0       Cubs   
1             5      NaN       NaN      NaN          0       0       Cubs   
2             5      1.0       NaN      NaN          0       0       Cubs   
3             5      1.0       NaN      NaN          0       0       Cubs   
4             5      1.0       NaN      NaN          0       0       Cubs   
5             5      1.0       NaN      NaN          0       0       Cubs   
6             5      NaN       1.0      1.0          0       0       Cubs   
7             5      NaN       1.0      1.0          0       0       Cubs   
8             5      NaN       1.0      1.0          0       0       Cubs   
9             5      NaN       1.0      1.0         -1       1       Cubs   
10            5      NaN       NaN      1.0         -1       1       Cubs   
11            5      NaN       NaN      1.0         -1       1       Cubs   
12            5      NaN       NaN      1.0         -1       1       Cubs   
13            5      NaN       NaN      1.0         -1       1       Cubs   
14            5      NaN       NaN      NaN         -1       0  Cardinals   
15            5      NaN       NaN      NaN         -1       0  Cardinals   
16            5      NaN       NaN      NaN         -1       0  Cardinals   
17            5      1.0       NaN      NaN         -1       0  Cardinals   
18            5      1.0       NaN      NaN         -1       0  Cardinals   
19            5      1.0       NaN      NaN         -1       0  Cardinals   
20            5      1.0       NaN      NaN         -1       0  Cardinals   
21            5      1.0       NaN      NaN         -1       0  Cardinals   
22            5      1.0       NaN      NaN         -1       0  Cardinals   
23            5      1.0       NaN      NaN         -1       0  Cardinals   
24            5      1.0       NaN      NaN         -1       0  Cardinals   
25            5      1.0       1.0      NaN         -1       0  Cardinals   
26            5      1.0       NaN      NaN         -1       0  Cardinals   
27            5      1.0       NaN      NaN         -1       0  Cardinals   
28            5      1.0       NaN      NaN         -1       0  Cardinals   
29            5      1.0       NaN      NaN         -1       0  Cardinals   
..          ...      ...       ...      ...        ...     ...        ...   
427           5      NaN       NaN      NaN          0       2       Cubs   
428           5      NaN       NaN      NaN          0       2       Cubs   
429           5      NaN       NaN      NaN          0       2       Cubs   
430           5      NaN       NaN      NaN          0       2       Cubs   
431           5      NaN       NaN      NaN          0       2       Cubs   
432           5      NaN       NaN      NaN          0       2       Cubs   
433           5      NaN       NaN      NaN          0       2       Cubs   
434           5      NaN       NaN      NaN          0       2       Cubs   
435           5      NaN       NaN      NaN          0       2       Cubs   
436           5      NaN       NaN      NaN          0       2       Cubs   
437           5      NaN       NaN      NaN         -1       3       Cubs   
438           5      NaN       NaN      NaN         -1       3       Cubs   
439           5      NaN       NaN      NaN         -1       3       Cubs   
440           5      NaN       NaN      NaN         -1       2  Cardinals   
441           5      NaN       NaN      NaN         -1       2  Cardinals   
442           5      NaN       NaN      NaN         -1       2  Cardinals   
443           5      NaN       NaN      NaN         -1       2  Cardinals   
444           5      NaN       NaN      NaN         -1       2  Cardinals   
445           5      NaN       NaN      NaN         -1       2  Cardinals   
446           5      NaN       NaN      NaN         -1       2  Cardinals   
4

#### Getting weather // time 

In [505]:
weather6 = jason_parsed_6th['game']['innings'][4]['halfs'][1]['weather']['current_conditions']
weather6

{'cloud_cover': 100,
 'condition': 'Light Rain',
 'dew_point_f': 55,
 'humidity': 68,
 'obs_time': '2018-05-07T02:19:02.000Z',
 'temp_f': 66,
 'wind': {'direction': 'N', 'speed_mph': 0}}

In [506]:
May6 = May6.assign(**{'cloud_cover': 100,
  'condition': 'Light Rain',
  'dew_point_f': 55,
  'humidity': 68,
  'obs_time': '2018-05-07T02:19:02.000Z',
  'temp_f': 66, 'wind_direction':'N','wind_speed':0, 'Homegame?': 1, "Nightgame?":1}
                   )

In [507]:
May6

GamevsCubs  OnFirst  OnSecond  OnThird  PointDiff  Points       Team  \
0             5      NaN       NaN      NaN          0       0       Cubs   
1             5      NaN       NaN      NaN          0       0       Cubs   
2             5      1.0       NaN      NaN          0       0       Cubs   
3             5      1.0       NaN      NaN          0       0       Cubs   
4             5      1.0       NaN      NaN          0       0       Cubs   
5             5      1.0       NaN      NaN          0       0       Cubs   
6             5      NaN       1.0      1.0          0       0       Cubs   
7             5      NaN       1.0      1.0          0       0       Cubs   
8             5      NaN       1.0      1.0          0       0       Cubs   
9             5      NaN       1.0      1.0         -1       1       Cubs   
10            5      NaN       NaN      1.0         -1       1       Cubs   
11            5      NaN       NaN      1.0         -1       1       Cubs   
12            5      NaN       NaN      1.0         -1       1       Cubs   
13            5      NaN       NaN      1.0         -1       1       Cubs   
14            5      NaN       NaN      NaN         -1       0  Cardinals   
15            5      NaN       NaN      NaN         -1       0  Cardinals   
16            5      NaN       NaN      NaN         -1       0  Cardinals   
17            5      1.0       NaN      NaN         -1       0  Cardinals   
18            5      1.0       NaN      NaN         -1       0  Cardinals   
19            5      1.0       NaN      NaN         -1       0  Cardinals   
20            5      1.0       NaN      NaN         -1       0  Cardinals   
21            5      1.0       NaN      NaN         -1       0  Cardinals   
22            5      1.0       NaN      NaN         -1       0  Cardinals   
23            5      1.0       NaN      NaN         -1       0  Cardinals   
24            5      1.0       NaN      NaN         -1       0  Cardinals   
25            5      1.0       1.0      NaN         -1       0  Cardinals   
26            5      1.0       NaN      NaN         -1       0  Cardinals   
27            5      1.0       NaN      NaN         -1       0  Cardinals   
28            5      1.0       NaN      NaN         -1       0  Cardinals   
29            5      1.0       NaN      NaN         -1       0  Cardinals   
..          ...      ...       ...      ...        ...     ...        ...   
427           5      NaN       NaN      NaN          0       2       Cubs   
428           5      NaN       NaN      NaN          0       2       Cubs   
429           5      NaN       NaN      NaN          0       2       Cubs   
430           5      NaN       NaN      NaN          0       2       Cubs   
431           5      NaN       NaN      NaN          0       2       Cubs   
432           5      NaN       NaN      NaN          0       2       Cubs   
433           5      NaN       NaN      NaN          0       2       Cubs   
434           5      NaN       NaN      NaN          0       2       Cubs   
435           5      NaN       NaN      NaN          0       2       Cubs   
436           5      NaN       NaN      NaN          0       2       Cubs   
437           5      NaN       NaN      NaN         -1       3       Cubs   
438           5      NaN       NaN      NaN         -1       3       Cubs   
439           5      NaN       NaN      NaN         -1       3       Cubs   
440           5      NaN       NaN      NaN         -1       2  Cardinals   
441           5      NaN       NaN      NaN         -1       2  Cardinals   
442           5      NaN       NaN      NaN         -1       2  Cardinals   
443           5      NaN       NaN      NaN         -1       2  Cardinals   
444           5      NaN       NaN      NaN         -1       2  Cardinals   
445           5      NaN       NaN      NaN         -1       2  Cardinals   
446           5      NaN       NaN      NaN         -1       2  Cardinals   
4

In [508]:
May6.to_csv('may6', index_label = None)

### Merging and Cleaning

In [519]:
allgames = apr17.append(apr19).append(May4).append(May5).append(May6)

In [526]:
allgames.fillna(value = 0, inplace=True)

GamevsCubs  Homegame?  Nightgame?  OnFirst  OnSecond  OnThird  PointDiff  \
0             1        0.0         1.0      0.0       0.0      0.0          0   
1             1        0.0         1.0      0.0       0.0      0.0          0   
2             1        0.0         1.0      0.0       0.0      0.0          0   
3             1        0.0         1.0      0.0       0.0      0.0          0   
4             1        0.0         1.0      0.0       0.0      0.0          0   
5             1        0.0         1.0      0.0       0.0      0.0          0   
6             1        0.0         1.0      0.0       0.0      0.0          0   
7             1        0.0         1.0      0.0       0.0      0.0          0   
8             1        0.0         1.0      0.0       0.0      0.0          0   
9             1        0.0         1.0      0.0       0.0      0.0          0   
10            1        0.0         1.0      0.0       0.0      0.0          0   
11            1        0.0         1.0      0.0       0.0      0.0          0   
12            1        0.0         1.0      0.0       0.0      0.0          0   
13            1        0.0         1.0      1.0       0.0      0.0          0   
14            1        0.0         1.0      1.0       0.0      0.0          0   
15            1        0.0         1.0      0.0       0.0      0.0          0   
16            1        0.0         1.0      0.0       0.0      0.0          0   
17            1        0.0         1.0      0.0       0.0      0.0          0   
18            1        0.0         1.0      0.0       0.0      0.0          0   
19            1        0.0         1.0      0.0       0.0      0.0          0   
20            1        0.0         1.0      0.0       0.0      0.0          0   
21            1        0.0         1.0      0.0       0.0      0.0          0   
22            1        0.0         1.0      0.0       0.0      0.0          0   
23            1        0.0         1.0      0.0       0.0      0.0          0   
24            1        0.0         1.0      0.0       0.0      0.0          0   
25            1        0.0         1.0      1.0       0.0      0.0          0   
26            1        0.0         1.0      1.0       0.0      0.0          0   
27            1        0.0         1.0      1.0       0.0      0.0          0   
28            1        0.0         1.0      0.0       0.0      0.0          0   
29            1        0.0         1.0      0.0       0.0      0.0          0   
..          ...        ...         ...      ...       ...      ...        ...   
427           5        1.0         1.0      0.0       0.0      0.0          0   
428           5        1.0         1.0      0.0       0.0      0.0          0   
429           5        1.0         1.0      0.0       0.0      0.0          0   
430           5        1.0         1.0      0.0       0.0      0.0          0   
431           5        1.0         1.0      0.0       0.0      0.0          0   
432           5        1.0         1.0      0.0       0.0      0.0          0   
433           5        1.0         1.0      0.0       0.0      0.0          0   
434           5        1.0         1.0      0.0       0.0      0.0          0   
435           5        1.0         1.0      0.0       0.0      0.0          0   
436           5        1.0         1.0      0.0       0.0      0.0          0   
437           5        1.0         1.0      0.0       0.0      0.0         -1   
438           5        1.0         1.0      0.0       0.0      0.0         -1   
439           5        1.0         1.0      0.0       0.0      0.0         -1   
440           5        1.0         1.0      0.0       0.0      0.0         -1   
441           5        1.0         1.0      0.0       0.0      0.0         -1   
442           5        1.0         1.0      0.0       0.0      0.0         -1   
443           5        1.0         1.0      0.0       0.0      0.0         -1   
444           5        1.0         1

In [532]:
allgames.loc[allgames['hitter.id'] == 0]['pitcher.id']

217    0
308    0
309    0
84     0
217    0
223    0
247    0
256    0
257    0
177    0
185    0
284    0
260    0
261    0
429    0
Name: pitcher.id, dtype: object

**Removing NaNs** <br>
(When the pitcher, or player id = 0). It seems like there are 3 junk columns.

In [533]:
allgamesclean = allgames.drop(allgames.index[[217,308,309,84,217,223,247,256,257,177,185,284,260,261,429]])

In [534]:
allgamesclean.loc[allgamesclean['hitter.id'] == 0]['pitcher.id']

429    0
Name: pitcher.id, dtype: object

**Removing Cubs hits**

In [535]:
allgamesclean2 = allgamesclean.set_index('Team')
allgamesclean2 = allgamesclean2.drop(labels = 'Cubs')
allgamesclean3 = allgamesclean2.reset_index()

In [539]:
allgamesclean3

Team  GamevsCubs  Homegame?  Nightgame?  OnFirst  OnSecond  OnThird  \
0    Cardinals           1        0.0         1.0      0.0       0.0      0.0   
1    Cardinals           1        0.0         1.0      0.0       0.0      0.0   
2    Cardinals           1        0.0         1.0      0.0       0.0      0.0   
3    Cardinals           1        0.0         1.0      0.0       0.0      0.0   
4    Cardinals           1        0.0         1.0      0.0       0.0      0.0   
5    Cardinals           1        0.0         1.0      0.0       0.0      0.0   
6    Cardinals           1        0.0         1.0      0.0       0.0      0.0   
7    Cardinals           1        0.0         1.0      0.0       0.0      0.0   
8    Cardinals           1        0.0         1.0      0.0       0.0      0.0   
9    Cardinals           1        0.0         1.0      0.0       0.0      0.0   
10   Cardinals           1        0.0         1.0      0.0       0.0      0.0   
11   Cardinals           1        0.0         1.0      0.0       0.0      0.0   
12   Cardinals           1        0.0         1.0      0.0       0.0      0.0   
13   Cardinals           1        0.0         1.0      1.0       0.0      0.0   
14   Cardinals           1        0.0         1.0      1.0       0.0      0.0   
15   Cardinals           1        0.0         1.0      0.0       0.0      0.0   
16   Cardinals           1        0.0         1.0      0.0       0.0      0.0   
17   Cardinals           1        0.0         1.0      0.0       0.0      0.0   
18   Cardinals           1        0.0         1.0      0.0       0.0      0.0   
19   Cardinals           1        0.0         1.0      0.0       0.0      0.0   
20   Cardinals           1        0.0         1.0      1.0       0.0      0.0   
21   Cardinals           1        0.0         1.0      1.0       0.0      0.0   
22   Cardinals           1        0.0         1.0      1.0       0.0      0.0   
23   Cardinals           1        0.0         1.0      1.0       0.0      0.0   
24   Cardinals           1        0.0         1.0      1.0       0.0      0.0   
25   Cardinals           1        0.0         1.0      1.0       0.0      0.0   
26   Cardinals           1        0.0         1.0      1.0       0.0      0.0   
27   Cardinals           1        0.0         1.0      1.0       0.0      0.0   
28   Cardinals           1        0.0         1.0      1.0       0.0      0.0   
29   Cardinals           1        0.0         1.0      1.0       1.0      0.0   
..         ...         ...        ...         ...      ...       ...      ...   
864  Cardinals           5        1.0         1.0      0.0       0.0      0.0   
865  Cardinals           5        1.0         1.0      0.0       0.0      0.0   
866  Cardinals           5        1.0         1.0      0.0       0.0      0.0   
867  Cardinals           5        1.0         1.0      0.0       0.0      0.0   
868  Cardinals           5        1.0         1.0      0.0       0.0      0.0   
869  Cardinals           5        1.0         1.0      0.0       0.0      0.0   
870  Cardinals           5        1.0         1.0      0.0       0.0      0.0   
871  Cardinals           5        1.0         1.0      1.0       0.0      0.0   
872  Cardinals           5        1.0         1.0      1.0       0.0      0.0   
873  Cardinals           5        1.0         1.0      1.0       0.0      0.0   
874  Cardinals           5        1.0         1.0      1.0       0.0      0.0   
875  Cardinals           5        1.0         1.0      1.0       0.0      0.0   
876  Cardinals           5        1.0         1.0      1.0       0.0      0.0   
877  Cardinals           5        1.0         1.0      0.0       0.0      0.0   
878  Cardinals           5        1.0         1.0      0.0       0.0      0.0   
879  Cardinals           5        1.0         1.0      0.0       0.0      0.0   
880  Cardinals           5        1.0         1.0      0.0       0.0      0.0   
881  Cardinals           5        1.0    

** Selecting out the rows of interest for SQL **

In [540]:
hintputs = allgamesclean3.filter(items = ['OnFirst', 'OnSecond', 'OnThird', 'PointDiff', 'Points', 'Team',
        'flags.is_hit',
       'flags.is_passed_ball', 
       'hit_location', 'hit_type', 'hitter.id',
       'hitter.last_name', 'innings',
       'pitcher.hitter_hand', 'pitcher.id', 
       'pitcher.last_name', 'pitcher.pitch_count', 'pitcher.pitch_speed',
       'pitcher.pitch_type', 
       'pitcher.pitch_zone', 'pitcher.pitcher_hand', 'cloud_cover', 'condition', 'dew_point_f',
       'humidity', 'obs_time', 'temp_f', 'wind_direction', 'wind_speed',
       'Homegame?', 'Nightgame?'])

In [541]:
hintputs

OnFirst  OnSecond  OnThird  PointDiff  Points       Team flags.is_hit  \
0        0.0       0.0      0.0          0       0  Cardinals        False   
1        0.0       0.0      0.0          0       0  Cardinals        False   
2        0.0       0.0      0.0          0       0  Cardinals        False   
3        0.0       0.0      0.0          0       0  Cardinals        False   
4        0.0       0.0      0.0          0       0  Cardinals        False   
5        0.0       0.0      0.0          0       0  Cardinals        False   
6        0.0       0.0      0.0          0       0  Cardinals        False   
7        0.0       0.0      0.0          0       0  Cardinals        False   
8        0.0       0.0      0.0          0       0  Cardinals        False   
9        0.0       0.0      0.0          0       0  Cardinals        False   
10       0.0       0.0      0.0          0       0  Cardinals        False   
11       0.0       0.0      0.0          0       0  Cardinals        False   
12       0.0       0.0      0.0          0       0  Cardinals        False   
13       1.0       0.0      0.0          0       0  Cardinals        False   
14       1.0       0.0      0.0          0       0  Cardinals        False   
15       0.0       0.0      0.0          0       0  Cardinals        False   
16       0.0       0.0      0.0          0       0  Cardinals        False   
17       0.0       0.0      0.0          0       0  Cardinals        False   
18       0.0       0.0      0.0          0       0  Cardinals        False   
19       0.0       0.0      0.0          0       0  Cardinals        False   
20       1.0       0.0      0.0          0       0  Cardinals        False   
21       1.0       0.0      0.0          0       0  Cardinals        False   
22       1.0       0.0      0.0          0       0  Cardinals        False   
23       1.0       0.0      0.0          0       0  Cardinals        False   
24       1.0       0.0      0.0          0       0  Cardinals        False   
25       1.0       0.0      0.0          0       0  Cardinals        False   
26       1.0       0.0      0.0          0       0  Cardinals        False   
27       1.0       0.0      0.0          0       0  Cardinals        False   
28       1.0       0.0      0.0          0       0  Cardinals        False   
29       1.0       1.0      0.0          0       0  Cardinals        False   
..       ...       ...      ...        ...     ...        ...          ...   
864      0.0       0.0      0.0          0       2  Cardinals        False   
865      0.0       0.0      0.0          0       2  Cardinals        False   
866      0.0       0.0      0.0          0       2  Cardinals        False   
867      0.0       0.0      0.0          0       2  Cardinals        False   
868      0.0       0.0      0.0          0       2  Cardinals        False   
869      0.0       0.0      0.0          0       2  Cardinals        False   
870      0.0       0.0      0.0          0       2  Cardinals        False   
871      1.0       0.0      0.0          0       2  Cardinals        False   
872      1.0       0.0      0.0          0       2  Cardinals        False   
873      1.0       0.0      0.0          0       2  Cardinals        False   
874      1.0       0.0      0.0          0       2  Cardinals        False   
875      1.0       0.0      0.0          0       2  Cardinals        False   
876      1.0       0.0      0.0          0       2  Cardinals        False   
877      0.0       0.0      0.0         -1       2  Cardinals        False   
878      0.0       0.0      0.0         -1       2  Cardinals        False   
879      0.0       0.0      0.0         -1       2  Cardinals        False   
880      0.0       0.0      0.0         -1       2  Cardinals        False   
881      0.0       0.0      0.0         -1       2  Cardinals        False   
882      0.0       0.0      0.0         -1       2  Cardinals        False   
883      0.0       0.0     

In [542]:
hintputs.to_csv('forsqlin', index_label = None)

### EDA

In [557]:
hintputs2 = hintputs.groupby(['hit_type'])

In [585]:
hintputs2['hit_location'].value_counts()

hit_type  hit_location
0         0               771
FB        15                9
          10                3
          11                3
          13                2
          6                 2
          7                 2
          9                 2
          1                 1
          14                1
          2                 1
          8                 1
GB        22               16
          21                8
          23                8
          27                6
          24                5
          25                4
          13                3
          15                3
          11                2
          20                1
          29                1
LD        11                6
          13                5
          15                5
          10                3
          14                3
          6                 3
          1                 1
          12                1
          18                1
          21     